In [1]:
# conda install scikit-learn
# install from: http://docs.python-requests.org/en/master/
# to fix ssl installation of python packages issue
# curl https://bootstrap.pypa.io/get-pip.py | python3
# instructions to setup virtualenv
# https://www.tensorflow.org/install/install_mac
# pip3 install -r requirements.txt
# https://www.datacamp.com/community/tutorials/tensorflow-tutorial
# https://github.com/jtopor/CUNY-MSDA-661/blob/master/CIFAR-100/TF-Layers-CIFAR-100-v2.py
# feature columns
# https://data-flair.training/blogs/tensorflow-wide-and-deep-learning/

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import requests
import cv2
import h5py
import scipy.misc
import numpy as np
import csv
import sklearn.model_selection as model
import pickle 
import tensorflow as tf

from csv import DictReader
from urllib.request import urlopen
from matplotlib.pyplot import imshow
from fr_utils import *
from inception_blocks_v2 import *
from skimage import transform
from tensorflow.contrib import learn
from tensorflow.contrib.learn.python.learn.estimators import model_fn as model_fn_lib

%matplotlib inline
%load_ext autoreload
%autoreload

learning_rate = 0.001
IMAGE_HEIGHT = 32
IMAGE_WIDTH = 32
IMAGE_DEPTH = 3

np.set_printoptions(threshold=np.nan)

/Library/Frameworks/Python.framework/Versions/3.5/lib/python3.5/importlib/_bootstrap.py:222: RuntimeWarning: compiletime version 3.6 of module 'tensorflow.python.framework.fast_tensor_util' does not match runtime version 3.5
  return f(*args, **kwds)
Using TensorFlow backend.


In [2]:
def convert_input_format(data):    
    return np.transpose(
        np.reshape(data, (-1, 32, 32, 3), order="F"),
        axes=(0, 2, 1, 3)
    )

def convert_output_labels(data):
    return np.asarray(data['fine_labels'], dtype=np.int32)

def one_hot_labels(labels):
    return tf.one_hot(indices=tf.cast(labels, tf.int32), depth=100)

def unpickle(file):
    fo = open(file, "rb")
    dict = pickle.load(fo, encoding="latin1")
    fo.close()
    return dict

In [3]:
def conv_layer(input_layer, filters=32, kernel_size=[5,5]):
    # setting up the conv layer, with stride and padding
    return tf.layers.conv2d(
        inputs=input_layer,
        filters=filters,
        kernel_size=kernel_size,
        padding="same",
        activation=tf.nn.relu
    )

def maxpool_layer(conv, pool_size=[2,2], strides=2):
    return tf.layers.max_pooling2d(
        inputs=conv, pool_size=pool_size, strides=strides
    )

def dropout_layer(inputs, mode, rate=0.25):
    
    return tf.layers.dropout(
        inputs=inputs, rate=rate, training=mode == learn.ModeKeys.TRAIN
    )

def dense_layer(inputs, units, activation=tf.nn.relu):
    return tf.layers.dense(inputs=inputs, units=units, activation=activation)

def determine_loss(labels, logits, mode):
    print(mode)
#     if mode != learn.ModeKeys.INFER:
    return tf.losses.softmax_cross_entropy (
        onehot_labels=one_hot_labels(labels),
        logits=logits
    )
#     else:
#         return None
    
def determine_train_op(loss, mode):
    print(mode)
#     if mode == learn.ModeKeys.TRAIN:
    return tf.contrib.layers.optimize_loss (
        loss=loss, 
        global_step=tf.contrib.framework.get_global_step(),
        learning_rate=0.0001,
        optimizer="Adam"
    )
#     else:
#         return None
    
def generate_predictions(logits):
    return {
        "classes": tf.argmax(input=logits, axis=1),
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }

def cnn_model(features, labels, mode): 
    mode = learn.ModeKeys.TRAIN if mode == "train" else learn.ModeKeys.INFER
    input_layer = tf.convert_to_tensor(features)
    
    # cnn layer 1
    conv1 = conv_layer(input_layer)
    conv2 = conv_layer(conv1)
    
    # pooling layer 1 
    pool1 = maxpool_layer(conv2)
    
    # dropout operation
    dropout1 = dropout_layer(pool1, mode)
    
    # cnn layer 2 
    conv3 = conv_layer(dropout1, 64, [3, 3])
    conv4 = conv_layer(conv3, 64, [3, 3])
    
    # pooling layer 2
    pool2 = maxpool_layer(conv4)
    
    # dropout operation
    dropout2 = dropout_layer(pool2, mode)
    
    # flatten tensor into a batch of vectors
    pool2_flat = tf.reshape(dropout2, [-1, 8 * 8 * 64])
    
    # dense layer 
    dense1 = dense_layer(pool2_flat, 1024)
    
    # flatten tensor again
    dropout3 = dropout_layer(dense1, mode, 0.4)
    
    # second fully connected layer 
    dense2 = tf.layers.dense(inputs=dropout3, units=512)
    
    # dropout operation
    dropout4 = dropout_layer(dense2, mode, 0.4)
    
    # logits layer
    logits = tf.layers.dense(inputs=dropout4, units=100)
    
    loss = determine_loss(labels, logits, mode)
    train_op = determine_train_op(loss, mode)
    predictions = generate_predictions(logits)
    
    return model_fn_lib.ModelFnOps(
        mode=mode, predictions=predictions, loss=loss, train_op=train_op
    )


In [4]:
def generate_accuracy_metric():
    # configure the accuracy metric
    return {
        "accuracy": learn.MetricSpec (
            metric_fn=tf.metrics.accuracy, prediction_key="classes"
        )
    }

def serving_input_fn():
    """An input receiver that expects a serialized tf.Example."""

    # feature spec dictionary  determines our input parameters for the model
    feature_spec = {
        'images': tf.FixedLenFeature(shape=[1], dtype=tf.float32)
    }

    # the inputs will be initially fed as strings with data serialized by
    # Google ProtoBuffers
    serialized_tf_example = tf.placeholder(
        dtype=tf.string, shape=[1], name='input_example_tensor')
    receiver_tensors = {'images': serialized_tf_example}

    # deserialize input
    features = tf.parse_example(serialized_tf_example, feature_spec)
    return tf.estimator.export.ServingInputReceiver(features, receiver_tensors)
    
def print_evaluate_model(cifar_classifier, data, labels, epoches, subset):
    small_train = np.array_split(data, epoches)[subset]
    small_labels = np.array_split(labels, epoches)[subset]
    evaluate_results = cifar_classifier.evaluate(
        x=small_train, y=small_labels, metrics=generate_accuracy_metric()
    )
    print(evaluate_results)
    return evaluate_results

def setup_and_train_model():
    dataset = unpickle("./datasets/cifar-100-parsed/cifar-100-python/train")
    data = dataset["data"]
    data = data.astype("float32")
    train_data = convert_input_format(data)
    train_labels = convert_output_labels(dataset)
    model_ckpt = "./models/cifar-100"
    
    deep_columns = [
        tf.feature_column.numeric_column('beaver'),
        tf.feature_column.numeric_column('dolphin'),
        tf.feature_column.numeric_column('otter'),
        tf.feature_column.numeric_column('seal'),
        tf.feature_column.numeric_column('whale'),
        tf.feature_column.numeric_column('aquarium fish'),
        tf.feature_column.numeric_column('flatfish'),
        tf.feature_column.numeric_column('ray'),
        tf.feature_column.numeric_column('shark'),
        tf.feature_column.numeric_column('trout'),
        tf.feature_column.numeric_column('orchids'),
        tf.feature_column.numeric_column('poppies'),
        tf.feature_column.numeric_column('roses'),
        tf.feature_column.numeric_column('sunflowers'),
        tf.feature_column.numeric_column('sunflowers'),
        tf.feature_column.numeric_column('bottles'),
        tf.feature_column.numeric_column('bowls'),
        tf.feature_column.numeric_column('cans'),
        tf.feature_column.numeric_column('cups'),
        tf.feature_column.numeric_column('plates'),
        tf.feature_column.numeric_column('apples'),
        tf.feature_column.numeric_column('mushrooms'),
        tf.feature_column.numeric_column('oranges'),
        tf.feature_column.numeric_column('pears'),
        tf.feature_column.numeric_column('sweet peppers'),
        tf.feature_column.numeric_column('clock'),
        tf.feature_column.numeric_column('computer keyboard'),
        tf.feature_column.numeric_column('lamp'),
        tf.feature_column.numeric_column('telephone'),
        tf.feature_column.numeric_column('television'),
        tf.feature_column.numeric_column('bed'),
        tf.feature_column.numeric_column('chair'),
        tf.feature_column.numeric_column('couch'),
        tf.feature_column.numeric_column('table'),
        tf.feature_column.numeric_column('wardrobe'),
        tf.feature_column.numeric_column('bee'),
        tf.feature_column.numeric_column('beetle'),
        tf.feature_column.numeric_column('butterfly'),
        tf.feature_column.numeric_column('caterpillar'),
        tf.feature_column.numeric_column('cockroach'),
        tf.feature_column.numeric_column('bear'),
        tf.feature_column.numeric_column('leopard'),
        tf.feature_column.numeric_column('lion'),
        tf.feature_column.numeric_column('tiger'),
        tf.feature_column.numeric_column('wolf'),
        tf.feature_column.numeric_column('bridge'),
        tf.feature_column.numeric_column('castle'),
        tf.feature_column.numeric_column('house'),
        tf.feature_column.numeric_column('road'),
        tf.feature_column.numeric_column('skyscraper'),
        tf.feature_column.numeric_column('cloud'),
        tf.feature_column.numeric_column('forest'),
        tf.feature_column.numeric_column('mountain'),
        tf.feature_column.numeric_column('plain'),
        tf.feature_column.numeric_column('sea'),
        tf.feature_column.numeric_column('camel'),
        tf.feature_column.numeric_column('cattle'),
        tf.feature_column.numeric_column('chimpanzee'),
        tf.feature_column.numeric_column('elephant'),
        tf.feature_column.numeric_column('kangaroo'),
        tf.feature_column.numeric_column('fox'),
        tf.feature_column.numeric_column('porcupine'),
        tf.feature_column.numeric_column('possum'),
        tf.feature_column.numeric_column('raccoon'),
        tf.feature_column.numeric_column('skunk'),
        tf.feature_column.numeric_column('crab'),
        tf.feature_column.numeric_column('lobster'),
        tf.feature_column.numeric_column('snail'),
        tf.feature_column.numeric_column('spider'),
        tf.feature_column.numeric_column('worm'),
        tf.feature_column.numeric_column('baby'),
        tf.feature_column.numeric_column('boy'),
        tf.feature_column.numeric_column('girl'),
        tf.feature_column.numeric_column('man'),
        tf.feature_column.numeric_column('woman'),
        tf.feature_column.numeric_column('crocodile'),
        tf.feature_column.numeric_column('dinosaur'),
        tf.feature_column.numeric_column('lizard'),
        tf.feature_column.numeric_column('snake'),
        tf.feature_column.numeric_column('turtle'),
        tf.feature_column.numeric_column('hamster'),
        tf.feature_column.numeric_column('mouse'),
        tf.feature_column.numeric_column('rabbit'),
        tf.feature_column.numeric_column('shrew'),
        tf.feature_column.numeric_column('squirrel'),
        tf.feature_column.numeric_column('maple'),
        tf.feature_column.numeric_column('oak'),
        tf.feature_column.numeric_column('palm'),
        tf.feature_column.numeric_column('pine'),
        tf.feature_column.numeric_column('willow'),
        tf.feature_column.numeric_column('bicycle'),
        tf.feature_column.numeric_column('bus'),
        tf.feature_column.numeric_column('motorcycle'),
        tf.feature_column.numeric_column('pickup truck'),
        tf.feature_column.numeric_column('train'),
        tf.feature_column.numeric_column('lawn-mower'),
        tf.feature_column.numeric_column('rocket'),
        tf.feature_column.numeric_column('streetcar'),
        tf.feature_column.numeric_column('tank'),
        tf.feature_column.numeric_column('tractor')
    ]
    
    feature_spec = tf.feature_column.make_parse_example_spec(deep_columns)
    export_input_fn = tf.contrib.learn.build_parsing_serving_input_fn(feature_spec)
    
    exporter = tf.estimator.LatestExporter (
        name="Servo",
        serving_input_receiver_fn=export_input_fn,
        assets_extra=None,
        as_text=False,
        exports_to_keep=5
    )
    
    # create custom estimator
    cifar_classifier = learn.Estimator (
        model_fn=cnn_model, model_dir=model_ckpt
    )
    
    # log predictions
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook (
        tensors=tensors_to_log, every_n_iter=100
    )
    
    # train the model
    with tf.device("/cpu:0"):
        cifar_classifier.fit (
            x=train_data,
            y=train_labels,
            batch_size=64, 
            steps=5240,
            monitors=[logging_hook]
        )
    
    full_model_dir = cifar_classifier.export_savedmodel(
        model_ckpt, export_input_fn
    )
    return cifar_classifier


def test_model(cifar_classifier):
    dataset = unpickle("./datasets/cifar-100-parsed/cifar-100-python/test")
    data = dataset["data"]
    data = data.astype("float32")
    test_data = convert_input_format(data)
    test_labels = convert_output_labels(dataset)
    
    # evaluate all test data and print results
    acc = 0
    e_loss = 0
    n_batches = 20
    for i in range (0, n_batches - 1):
        small_eval =  np.array_split(test_data, n_batches)[i]
        small_labs =  np.array_split(test_labels, n_batches)[i]
        eval_results = cifar_classifier.evaluate(
          x=small_eval, y=small_labs, metrics=generate_accuracy_metric())
        print(eval_results)
        acc += eval_results["accuracy"]
        e_loss += eval_results["loss"]

    overall_acc = acc / n_batches
    overall_loss = e_loss/ n_batches
    print("Eval Accuracy = ", overall_acc)
    print("Eval Loss = ", overall_loss) 

In [5]:
classifier = setup_and_train_model()

Instructions for updating:
Please use tf.estimator.export.build_parsing_serving_input_receiver_fn.
Instructions for updating:
Please replace uses of any Estimator from tf.contrib.learn with an Estimator from tf.estimator.*
Instructions for updating:
When switching to tf.estimator.Estimator, use tf.estimator.RunConfig instead.
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_evaluation_master': '', '_session_config': None, '_train_distribute': None, '_device_fn': None, '_tf_config': gpu_options {
  per_process_gpu_memory_fraction: 1.0
}
, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x13aa3b0b8>, '_log_step_count_steps': 100, '_model_dir': '/tmp/cifar100', '_num_worker_replicas': 0, '_num_ps_replicas': 0, '_save_checkpoints_steps': None, '_save_summary_steps': 100, '_is_chief': True, '_keep_checkpoint_every_n_hours': 10000, '_master': '', '_task_type': None, '_task_id': 0, '_save_checkpoints_secs': 600, '_tf_random_seed': None, '_en

INFO:tensorflow:loss = 3.7005284, step = 5241
INFO:tensorflow:global_step/sec: 2.54036
INFO:tensorflow:probabilities = [[0.00567349 0.00353775 0.00628022 0.03653185 0.01221283 0.01246046
  0.00838304 0.01426399 0.00783014 0.01120737 0.01110231 0.00791739
  0.00833046 0.00834627 0.03557005 0.01181547 0.02507012 0.00147584
  0.01027848 0.01294967 0.01455933 0.01709486 0.00778744 0.00134871
  0.00877286 0.01310483 0.014818   0.00902023 0.00460381 0.01749137
  0.00199222 0.01105932 0.01289352 0.00700482 0.01178952 0.00739975
  0.00517893 0.00500571 0.00711632 0.00607785 0.01515273 0.01959654
  0.00871278 0.00882559 0.00509276 0.01261809 0.01174062 0.00122924
  0.01298298 0.0027755  0.01118895 0.02364108 0.00134972 0.00151189
  0.00573475 0.01203493 0.00380318 0.01108141 0.01409652 0.00233249
  0.00105401 0.00286655 0.00326482 0.00400327 0.01853235 0.00407289
  0.01597097 0.00875807 0.00200696 0.00473991 0.00833394 0.00125745
  0.01072377 0.01094139 0.00899515 0.0605991  0.00204179 0.006309

INFO:tensorflow:loss = 3.787683, step = 5341 (39.456 sec)
INFO:tensorflow:global_step/sec: 2.49197
INFO:tensorflow:probabilities = [[0.01317843 0.02425057 0.01457553 0.00998879 0.01502813 0.00945454
  0.01755155 0.00752819 0.00627356 0.01405819 0.00788494 0.01122198
  0.0073963  0.00666982 0.01866159 0.01396506 0.00899621 0.00427234
  0.01270746 0.007262   0.00635882 0.0084014  0.00653583 0.00573968
  0.00602917 0.00845246 0.00938108 0.01635098 0.00746875 0.01148492
  0.00755976 0.00990055 0.00699806 0.0102197  0.0212501  0.01263571
  0.015448   0.00646409 0.01200031 0.00557446 0.0070804  0.00827574
  0.01441753 0.01210618 0.01124807 0.01344923 0.00990668 0.00670302
  0.00703956 0.00415115 0.00814642 0.01223241 0.00426291 0.01073329
  0.0096487  0.01235094 0.00910997 0.01735954 0.00885295 0.00770421
  0.00649642 0.00631581 0.0082494  0.01403906 0.01413163 0.01356521
  0.00767975 0.00979593 0.00438521 0.01866217 0.00804446 0.00626885
  0.01131201 0.00428575 0.01094314 0.0081563  0.00413

INFO:tensorflow:loss = 3.4401693, step = 5441 (40.050 sec)
INFO:tensorflow:global_step/sec: 1.86454
INFO:tensorflow:probabilities = [[0.00475549 0.01841923 0.00173932 0.01396368 0.00586363 0.00478981
  0.00359883 0.00651676 0.01555222 0.00313456 0.0084264  0.00601842
  0.00860548 0.07709609 0.00884326 0.01116847 0.00603902 0.00771894
  0.0047882  0.01411656 0.00463858 0.01383865 0.01034064 0.00079618
  0.00222842 0.00728096 0.00401656 0.0036221  0.00158472 0.01884366
  0.00145568 0.00644359 0.00532648 0.00656472 0.00311178 0.00653189
  0.0012671  0.0144567  0.00143937 0.00501326 0.00504433 0.01269341
  0.0022486  0.00229285 0.00419608 0.01141593 0.00790808 0.0039508
  0.07445134 0.00194025 0.00235873 0.00739235 0.00530655 0.00209179
  0.00172985 0.01018713 0.0094198  0.00432149 0.10753976 0.01081553
  0.00174395 0.00247344 0.00260431 0.0038644  0.00523883 0.00170076
  0.00312075 0.00145487 0.00495798 0.00074715 0.00427796 0.00155897
  0.00641344 0.00123671 0.00426322 0.00812543 0.00156

INFO:tensorflow:loss = 3.5878732, step = 5541 (53.697 sec)
INFO:tensorflow:global_step/sec: 2.16242
INFO:tensorflow:probabilities = [[0.00001048 0.00006376 0.00040574 0.00000209 0.00000151 0.0000098
  0.0001619  0.0000156  0.00000406 0.6601713  0.0000272  0.10543607
  0.00000519 0.00010045 0.00000647 0.00000156 0.03814751 0.00003523
  0.00002864 0.00000207 0.00015555 0.00000127 0.00003958 0.00000618
  0.00002712 0.00000218 0.00001159 0.00000256 0.00196054 0.00018854
  0.00002585 0.0000046  0.00041824 0.00000083 0.00000569 0.00291371
  0.00035276 0.00002007 0.00000272 0.00000701 0.00910039 0.15129474
  0.00001955 0.00004208 0.00000279 0.00014354 0.00543604 0.0000061
  0.000005   0.00002817 0.00000479 0.00000844 0.00000695 0.0005993
  0.01143184 0.00002453 0.00029897 0.00009501 0.00001217 0.0000398
  0.0000057  0.00012862 0.00017465 0.00000194 0.00002595 0.0000037
  0.00001424 0.00004049 0.00000002 0.00477913 0.00010293 0.00003664
  0.0006463  0.00001387 0.00000066 0.00000142 0.00059624 

...

INFO:tensorflow:loss = 3.3041847, step = 10141 (50.683 sec)
INFO:tensorflow:global_step/sec: 1.72408
INFO:tensorflow:probabilities = [[0.00000263 0.00040093 0.0000829  0.00026224 0.00017484 0.00003083
  0.0000258  0.00052249 0.00000553 0.00003685 0.00030067 0.00002395
  0.00024467 0.00003962 0.00011412 0.00002099 0.00006258 0.00001198
  0.00006653 0.00002115 0.00001609 0.00003563 0.00041288 0.01321733
  0.00018937 0.0000314  0.00011296 0.0008677  0.00040474 0.00001196
  0.6402903  0.00000284 0.00313989 0.00000905 0.00001057 0.0000301
  0.0000053  0.00001872 0.00002593 0.00332721 0.00324961 0.00000135
  0.00000064 0.000011   0.00161774 0.00112664 0.00006373 0.00002263
  0.00000729 0.004071   0.00008201 0.00000102 0.00004981 0.00000896
  0.00007784 0.00185559 0.00021149 0.00000982 0.00001609 0.0002915
  0.00008272 0.00019739 0.00016714 0.00001322 0.00019196 0.00030194
  0.00012371 0.02038035 0.00010669 0.00349379 0.00002096 0.00111609
  0.06006873 0.16850734 0.00005727 0.0002129  0.00061

INFO:tensorflow:loss = 2.965272, step = 10241 (58.005 sec)
INFO:tensorflow:Saving checkpoints for 10334 into /tmp/cifar100/model.ckpt.
INFO:tensorflow:global_step/sec: 1.90047
INFO:tensorflow:probabilities = [[0.00349712 0.00311326 0.02672671 0.00243431 0.00198156 0.03338889
  0.00147487 0.0027283  0.00293029 0.00684906 0.03997171 0.01172053
  0.00243402 0.00295625 0.00125983 0.00409142 0.01977292 0.00125641
  0.00720402 0.00442792 0.06299532 0.00097982 0.01876125 0.01641539
  0.01351    0.04770019 0.02505521 0.00407904 0.01594732 0.00453852
  0.00578859 0.00164294 0.0130695  0.00352149 0.00252383 0.00554385
  0.02081515 0.00440391 0.00153209 0.02125577 0.01790794 0.00172643
  0.00105552 0.00108683 0.02313786 0.01638635 0.0046962  0.00137037
  0.00035253 0.00176765 0.01137214 0.001649   0.00053976 0.00466804
  0.00437078 0.00438988 0.0010139  0.00351083 0.00106275 0.00100428
  0.00222623 0.01830936 0.00198749 0.00160832 0.00414932 0.01366137
  0.00419994 0.00383855 0.0172715  0.0085212

INFO:tensorflow:loss = 2.9968276, step = 10341 (52.569 sec)
INFO:tensorflow:global_step/sec: 2.05756
INFO:tensorflow:probabilities = [[0.00057649 0.00647182 0.01246208 0.0045557  0.01729946 0.01408936
  0.00226296 0.00648991 0.02449419 0.00246842 0.01275833 0.02224915
  0.02095729 0.01895335 0.00181153 0.00251717 0.00754138 0.00321504
  0.00148486 0.00570083 0.00393883 0.0172691  0.02787299 0.00076653
  0.00240834 0.01283896 0.0236488  0.01015617 0.0023468  0.00885733
  0.00146798 0.00624168 0.00940971 0.00759265 0.00450257 0.00827599
  0.00528792 0.0243253  0.00650621 0.0118887  0.02057209 0.00402736
  0.01929185 0.00582823 0.00644896 0.00761527 0.01524581 0.00194302
  0.01109475 0.00124933 0.00642493 0.01417611 0.00200645 0.00091643
  0.0009818  0.00920274 0.00260597 0.00110068 0.03595826 0.00708211
  0.00107327 0.01720085 0.00044831 0.01582054 0.02741735 0.00494153
  0.04479711 0.00186492 0.00444426 0.00311426 0.00211152 0.00140095
  0.00571415 0.00160859 0.01272706 0.02029251 0.002

INFO:tensorflow:loss = 2.9640126, step = 10441 (48.631 sec)
INFO:tensorflow:Saving checkpoints for 10480 into /tmp/cifar100/model.ckpt.
INFO:tensorflow:Loss for final step: 3.0446444.
Instructions for updating:
Switch to tf.estimator.Exporter and associated utilities.
Instructions for updating:
Switch to tf.estimator.Exporter and associated utilities.
Instructions for updating:
Switch to tf.estimator.Exporter and associated utilities.


TypeError: Failed to convert object of type <class 'dict'> to Tensor. Contents: {'apples': <tf.Tensor 'ParseExample/ParseExample:0' shape=(?, 1) dtype=float32>, 'flatfish': <tf.Tensor 'ParseExample/ParseExample:33' shape=(?, 1) dtype=float32>, 'streetcar': <tf.Tensor 'ParseExample/ParseExample:81' shape=(?, 1) dtype=float32>, 'mouse': <tf.Tensor 'ParseExample/ParseExample:50' shape=(?, 1) dtype=float32>, 'baby': <tf.Tensor 'ParseExample/ParseExample:2' shape=(?, 1) dtype=float32>, 'kangaroo': <tf.Tensor 'ParseExample/ParseExample:39' shape=(?, 1) dtype=float32>, 'skyscraper': <tf.Tensor 'ParseExample/ParseExample:76' shape=(?, 1) dtype=float32>, 'lizard': <tf.Tensor 'ParseExample/ParseExample:44' shape=(?, 1) dtype=float32>, 'road': <tf.Tensor 'ParseExample/ParseExample:68' shape=(?, 1) dtype=float32>, 'crab': <tf.Tensor 'ParseExample/ParseExample:27' shape=(?, 1) dtype=float32>, 'palm': <tf.Tensor 'ParseExample/ParseExample:56' shape=(?, 1) dtype=float32>, 'possum': <tf.Tensor 'ParseE

In [35]:
test_model(classifier)

infer
infer
INFO:tensorflow:Starting evaluation at 2018-08-03-06:27:22
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/cifar100/model.ckpt-33528
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-08-03-06:27:27
INFO:tensorflow:Saving dict for global step 33528: accuracy = 0.424, global_step = 33528, loss = 2.4908679
{'global_step': 33528, 'loss': 2.4908679, 'accuracy': 0.424}
infer
infer
INFO:tensorflow:Starting evaluation at 2018-08-03-06:27:31
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/cifar100/model.ckpt-33528
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-08-03-06:27:36
INFO:tensorflow:Saving dict for global step 33528: accuracy = 0.442, global_step = 33528, loss = 2.2866387
{'global_step': 33528, 'loss': 2.2866387, 'accuracy': 0.442}
infer
infer
INFO:t

{'global_step': 33528, 'loss': 2.2949243, 'accuracy': 0.448}
infer
infer
INFO:tensorflow:Starting evaluation at 2018-08-03-06:28:53
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/cifar100/model.ckpt-33528
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-08-03-06:28:56
INFO:tensorflow:Saving dict for global step 33528: accuracy = 0.448, global_step = 33528, loss = 2.304841
{'global_step': 33528, 'loss': 2.304841, 'accuracy': 0.448}
infer
infer
INFO:tensorflow:Starting evaluation at 2018-08-03-06:28:58
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/cifar100/model.ckpt-33528
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-08-03-06:29:01
INFO:tensorflow:Saving dict for global step 33528: accuracy = 0.42, global_step = 33528, loss = 2.4275591
{'global_step': 33528